In [1]:
import numpy as np
from finesse.cymath.cmatrix import KLUMatrix

mat = KLUMatrix(name="mirror_example")
In1 = mat.declare_equations(Neqs=1, index=0, name="I_In1", is_diagonal=True)
Out1 = mat.declare_equations(Neqs=1, index=1, name="I_Out1", is_diagonal=True)
In2 = mat.declare_equations(Neqs=1, index=2, name="I_In2", is_diagonal=True)
Out2 = mat.declare_equations(Neqs=1, index=3, name="I_Out2", is_diagonal=True)

mat.construct()
mat.print_matrix()


Matrix mirror_example: nnz=4 neqs=4
    (col, row) = value
    (0, 0) = (1+0j) : I_In1 mode=0 -> I_In1 mode=0
    (1, 1) = (1+0j) : I_Out1 mode=0 -> I_Out1 mode=0
    (2, 2) = (1+0j) : I_In2 mode=0 -> I_In2 mode=0
    (3, 3) = (1+0j) : I_Out2 mode=0 -> I_Out2 mode=0



In [2]:
a11 = mat.declare_submatrix_view(In1.from_idx, Out1.from_idx, "_In1->Out1", False)
a22 = mat.declare_submatrix_view(In2.from_idx, Out2.from_idx, "_In2->Out2", False)

a12 = mat.declare_submatrix_view(In1.from_idx, Out2.from_idx, "_In1->Out2", False)
a21 = mat.declare_submatrix_view(In2.from_idx, Out1.from_idx, "_In2->Out1", False)

mat.construct()
mat.print_matrix()

print(f"{a11.shape=}")


Matrix mirror_example: nnz=8 neqs=4
    (col, row) = value
    (0, 0) = (1+0j) : I_In1 mode=0 -> I_In1 mode=0
    (0, 1) = 0j     : I_In1 mode=0 -> I_Out1 mode=0
    (0, 3) = 0j     : I_In1 mode=0 -> I_Out2 mode=0
    (1, 1) = (1+0j) : I_Out1 mode=0 -> I_Out1 mode=0
    (2, 1) = 0j     : I_In2 mode=0 -> I_Out1 mode=0
    (2, 2) = (1+0j) : I_In2 mode=0 -> I_In2 mode=0
    (2, 3) = 0j     : I_In2 mode=0 -> I_Out2 mode=0
    (3, 3) = (1+0j) : I_Out2 mode=0 -> I_Out2 mode=0

a11.shape=(1, 1)


In [3]:
r = np.sqrt(0.9)
t = np.sqrt(0.1)

a11[:] = r
a22[:] = r
a12[:] = 1j * t
a21[:] = 1j * t

mat.print_matrix()

# print in dense format
np.set_printoptions(precision=1, linewidth=250)
print(mat.to_scipy_csc().todense())


Matrix mirror_example: nnz=8 neqs=4
    (col, row) = value
    (0, 0) = (1+0j)                    : I_In1 mode=0 -> I_In1 mode=0
    (0, 1) = (-0.9486832980505138+0j)  : I_In1 mode=0 -> I_Out1 mode=0
    (0, 3) = (-0-0.31622776601683794j) : I_In1 mode=0 -> I_Out2 mode=0
    (1, 1) = (1+0j)                    : I_Out1 mode=0 -> I_Out1 mode=0
    (2, 1) = (-0-0.31622776601683794j) : I_In2 mode=0 -> I_Out1 mode=0
    (2, 2) = (1+0j)                    : I_In2 mode=0 -> I_In2 mode=0
    (2, 3) = (-0.9486832980505138+0j)  : I_In2 mode=0 -> I_Out2 mode=0
    (3, 3) = (1+0j)                    : I_Out2 mode=0 -> I_Out2 mode=0

[[ 1. +0.j   0. +0.j   0. +0.j   0. +0.j ]
 [-0.9+0.j   1. +0.j   0. -0.3j  0. +0.j ]
 [ 0. +0.j   0. +0.j   1. +0.j   0. +0.j ]
 [ 0. -0.3j  0. +0.j  -0.9+0.j   1. +0.j ]]


In [4]:
mat.set_rhs(In1.from_idx, 1.0)

In [5]:
mat.print_rhs()

mat.factor()
mat.solve()

mat.print_rhs()


Vector mirror_example: neqs=4
    (row) = value
    (0) = (1+0j) : I_In1 mode=0
    (1) = 0j     : I_Out1 mode=0
    (2) = 0j     : I_In2 mode=0
    (3) = 0j     : I_Out2 mode=0


Vector mirror_example: neqs=4
    (row) = value
    (0) = (1+0j)                  : I_In1 mode=0
    (1) = (0.9486832980505138+0j) : I_Out1 mode=0
    (2) = 0j                      : I_In2 mode=0
    (3) = 0.31622776601683794j    : I_Out2 mode=0



In [6]:
import finesse
import numpy as np

model = finesse.Model()

np.set_printoptions(linewidth=200, precision=1)

model.parse(
    """
        l l1
        s s1 l1.p1 m1.p1
        m m1 R=0.9 T=0.1
    """
)
model.run(simulation_options={"debug_mode": True});


Matrix carrier: nnz=12 neqs=6
    (col, row) = value
    (0, 0) = (1+0j)                   : I,node=l1.p1.i,f=0,fidx=0,Neq=1 mode=0 -> I,node=l1.p1.i,f=0,fidx=0,Neq=1 mode=0
    (1, 1) = (1+0j)                   : I,node=l1.p1.o,f=0,fidx=1,Neq=1 mode=0 -> I,node=l1.p1.o,f=0,fidx=1,Neq=1 mode=0
    (1, 2) = (-1-0j)                  : I,node=l1.p1.o,f=0,fidx=1,Neq=1 mode=0 -> I,node=m1.p1.i,f=0,fidx=2,Neq=1 mode=0
    (2, 2) = (1+0j)                   : I,node=m1.p1.i,f=0,fidx=2,Neq=1 mode=0 -> I,node=m1.p1.i,f=0,fidx=2,Neq=1 mode=0
    (2, 3) = (-0.9486832980505138-0j) : I,node=m1.p1.i,f=0,fidx=2,Neq=1 mode=0 -> I,node=m1.p1.o,f=0,fidx=3,Neq=1 mode=0
    (2, 5) = -0.31622776601683794j    : I,node=m1.p1.i,f=0,fidx=2,Neq=1 mode=0 -> I,node=m1.p2.o,f=0,fidx=5,Neq=1 mode=0
    (3, 0) = (-1-0j)                  : I,node=m1.p1.o,f=0,fidx=3,Neq=1 mode=0 -> I,node=l1.p1.i,f=0,fidx=0,Neq=1 mode=0
    (3, 3) = (1+0j)                   : I,node=m1.p1.o,f=0,fidx=3,Neq=1 mode=0 -> I,node=m1.p1.o,f=

In [7]:
with model.built() as sim:
    carrier_solver = sim.carrier
    klu_mat = carrier_solver.M()
    klu_mat.print_matrix()
    klu_mat.print_rhs()


Matrix carrier: nnz=12 neqs=6
    (col, row) = value
    (0, 0) = (1+0j)                   : I,node=l1.p1.i,f=0,fidx=0,Neq=1 mode=0 -> I,node=l1.p1.i,f=0,fidx=0,Neq=1 mode=0
    (1, 1) = (1+0j)                   : I,node=l1.p1.o,f=0,fidx=1,Neq=1 mode=0 -> I,node=l1.p1.o,f=0,fidx=1,Neq=1 mode=0
    (1, 2) = (-1-0j)                  : I,node=l1.p1.o,f=0,fidx=1,Neq=1 mode=0 -> I,node=m1.p1.i,f=0,fidx=2,Neq=1 mode=0
    (2, 2) = (1+0j)                   : I,node=m1.p1.i,f=0,fidx=2,Neq=1 mode=0 -> I,node=m1.p1.i,f=0,fidx=2,Neq=1 mode=0
    (2, 3) = (-0.9486832980505138-0j) : I,node=m1.p1.i,f=0,fidx=2,Neq=1 mode=0 -> I,node=m1.p1.o,f=0,fidx=3,Neq=1 mode=0
    (2, 5) = -0.31622776601683794j    : I,node=m1.p1.i,f=0,fidx=2,Neq=1 mode=0 -> I,node=m1.p2.o,f=0,fidx=5,Neq=1 mode=0
    (3, 0) = (-1-0j)                  : I,node=m1.p1.o,f=0,fidx=3,Neq=1 mode=0 -> I,node=l1.p1.i,f=0,fidx=0,Neq=1 mode=0
    (3, 3) = (1+0j)                   : I,node=m1.p1.o,f=0,fidx=3,Neq=1 mode=0 -> I,node=m1.p1.o,f=

In [8]:
from finesse.cymath.cmatrix import KLUMatrix

mat = KLUMatrix(name="singular_example")
In1 = mat.declare_equations(Neqs=1, index=0, name="I_In1", is_diagonal=True)
Out1 = mat.declare_equations(Neqs=1, index=1, name="I_Out1", is_diagonal=True)
a12 = mat.declare_submatrix_view(In1.from_idx, Out1.from_idx, "_In1->Out1", False)
a21 = mat.declare_submatrix_view(Out1.from_idx, In1.from_idx, "_Out1->In1", False)

mat.construct()

a12[:] = 1
a21[:] = 1

mat.factor()

Exception: An error occurred in KLU during factoring: STATUS=1 (KLU_SINGULAR)

Matrix singular_example: nnz=4 neqs=2
    (col, row) = value
    (0, 0) = (1+0j)  : I_In1 mode=0 -> I_In1 mode=0
    (0, 1) = (-1+0j) : I_In1 mode=0 -> I_Out1 mode=0
    (1, 0) = (-1+0j) : I_Out1 mode=0 -> I_In1 mode=0
    (1, 1) = (1+0j)  : I_Out1 mode=0 -> I_Out1 mode=0


In [9]:
import numpy as np
import finesse


model = finesse.Model()

model.parse(
    """
    l l1 P=1
    s s1 l1.p1 m1.p1
    m m1 R=0.1 T=0.9
    """
)
with model.built() as sim:
    sim.run_carrier()
    for node, val in zip(
        sim.carrier.nodes.keys(), np.array(sim.carrier.M().rhs_view[0, :]),
        strict=True
    ):
        print(node, val)

l1.p1.i (0.447213595499958+0j)
l1.p1.o (1.4142135623730951+0j)
m1.p1.i (1.4142135623730951+0j)
m1.p1.o (0.447213595499958+0j)
m1.p2.i 0j
m1.p2.o 1.3416407864998738j
